In [78]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.metrics import classification_report
from sklearn.preprocessing import MinMaxScaler, StandardScaler,LabelEncoder
from sklearn.decomposition import PCA
import sqlite3
import copy
import plotly.express as px


In [84]:
# Connect to the sqlite db file and retrieve data as Pandas data frame.
# cnx = sqlite3.connect('FPA_FOD_20170508.sqlite')
# sql = "select * from fires"
# df = pd.read_sql_query(sql, cnx)

In [156]:
df = pd.read_csv('FW_Veg_Rem_Combined.csv')
df['disc_clean_date'] = pd.to_datetime(df['disc_clean_date'])
# df.sort_values(by='disc_clean_date', inplace = True) 

In [157]:
df.head()

Unnamed: 0.1  Unnamed: 0 fire_name  fire_size fire_size_class  \
0             0           0       NaN       10.0               C   
1             1           1       NaN        3.0               B   
2             2           2       NaN       60.0               C   
3             3           3    WNA  1        1.0               B   
4             4           4       NaN        2.0               B   

    stat_cause_descr   latitude   longitude state disc_clean_date  ...  \
0  Missing/Undefined  18.105072  -66.753044    PR      2007-02-11  ...   
1              Arson  35.038330  -87.610000    TN      2006-12-11  ...   
2              Arson  34.947800  -88.722500    MS      2004-02-29  ...   
3     Debris Burning  39.641400 -119.308300    NV      2005-06-06  ...   
4      Miscellaneous  30.700600  -90.591400    LA      1999-09-22  ...   

  Wind_cont Hum_pre_30 Hum_pre_15  Hum_pre_7   Hum_cont Prec_pre_30  \
0  3.250413  78.216590  76.793750  76.381579  78.724370         0.0   
1  2.122320  70.840000  65.858911  55.505882  81.682678        59.8   
2  3.369050  75.531629  75.868613  76.812834  65.063800       168.8   
3  0.000000  44.778429  37.140811  35.353846   0.000000        10.4   
4 -1.000000  -1.000000  -1.000000  -1.000000  -1.000000        -1.0   

   Prec_pre_15 Prec_pre_7 Prec_cont  remoteness  
0          0.0        0.0       0.0    0.017923  
1          8.4        0.0      86.8    0.184355  
2         42.2       18.1     124.5    0.194544  
3          7.2        0.0       0.0    0.487447  
4         -1.0       -1.0      -1.0    0.214633  

[5 rows x 43 columns]

In [158]:
# Define a mapping to convert month names to numeric representation
month_to_number = {
    'Jan': 1, 'Feb': 2, 'Mar': 3, 'Apr': 4, 'May': 5, 'Jun': 6,
    'Jul': 7, 'Aug': 8, 'Sep': 9, 'Oct': 10, 'Nov': 11, 'Dec': 12
}

df1 = copy.copy(df[['discovery_month', 'state']])

df2 = df1.groupby('discovery_month').count().reset_index()

custom_month_order = ['Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']

# Sort the DataFrame by the 'Month' column using the custom order
df2['discovery_month'] = pd.Categorical(df2['discovery_month'], categories=custom_month_order, ordered=True)
df2.sort_values(by='discovery_month', inplace=True)
df2

# # # df2['state'] = df2['state'].astype(int)
fig = px.line_polar(df2, r=df2['state'], theta=df2['discovery_month'],line_close=True,template="plotly_dark",)
fig.show()


# df1['discovery_month'] = pd.to_datetime(df['discovery_month'])
# df1
# entries_per_month = df1.groupby(pd.Grouper(key='discovery_month', freq='M')).size()
           

# print(df1['putout_time'])



C:\Users\didov\AppData\Local\Programs\Python\Python310\lib\site-packages\plotly\express\_core.py:271: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [159]:
min_fire_size = df['fire_size'].min()
max_fire_size = df['fire_size'].max()

print(max_fire_size)

df['fire_size_norm'] = (df['fire_size'] - min_fire_size) / (max_fire_size - min_fire_size)
df

606945.0


Unnamed: 0.1  Unnamed: 0 fire_name  fire_size fire_size_class  \
0                 0           0       NaN       10.0               C   
1                 1           1       NaN        3.0               B   
2                 2           2       NaN       60.0               C   
3                 3           3    WNA  1        1.0               B   
4                 4           4       NaN        2.0               B   
...             ...         ...       ...        ...             ...   
55362         55362       55362    IMPACT     6289.0               G   
55363         55363       55363     BUTTE    70868.0               G   
55364         55364       55364    WILLOW     5702.0               G   
55365         55365       55365    BARKER     3261.0               F   
55366         55366       55366    VALLEY    76067.0               G   

        stat_cause_descr   latitude   longitude state disc_clean_date  ...  \
0      Missing/Undefined  18.105072  -66.753044    PR      2007-02-11  ...   
1                  Arson  35.038330  -87.610000    TN      2006-12-11  ...   
2                  Arson  34.947800  -88.722500    MS      2004-02-29  ...   
3         Debris Burning  39.641400 -119.308300    NV      2005-06-06  ...   
4          Miscellaneous  30.700600  -90.591400    LA      1999-09-22  ...   
...                  ...        ...         ...   ...             ...  ...   
55362  Missing/Undefined  39.180000  -96.784167    KS      2015-10-15  ...   
55363  Missing/Undefined  38.342719 -120.695967    CA      2015-09-09  ...   
55364              Arson  37.262607 -119.511139    CA      2015-07-25  ...   
55365      Miscellaneous  40.604300 -123.080450    CA      2015-07-31  ...   
55366  Missing/Undefined  38.843988 -122.759707    CA      2015-09-12  ...   

      Hum_pre_30 Hum_pre_15  Hum_pre_7   Hum_cont Prec_pre_30 Prec_pre_15  \
0      78.216590  76.793750  76.381579  78.724370         0.0         0.0   
1      70.840000  65.858911  55.505882  81.682678        59.8         8.4   
2      75.531629  75.868613  76.812834  65.063800       168.8        42.2   
3      44.778429  37.140811  35.353846   0.000000        10.4         7.2   
4      -1.000000  -1.000000  -1.000000  -1.000000        -1.0        -1.0   
...          ...        ...        ...        ...         ...         ...   
55362  65.671410  61.839572  54.625698  55.042092        35.4         8.2   
55363  -1.000000  -1.000000  -1.000000  -1.000000        -1.0        -1.0   
55364  43.755556  43.755556  44.443975  35.924406         0.0         0.0   
55365  -1.000000  -1.000000  -1.000000  -1.000000        -1.0        -1.0   
55366  50.521912  46.310627  37.178571  58.063802         0.3         0.3   

       Prec_pre_7 Prec_cont remoteness  fire_size_norm  
0             0.0       0.0   0.017923    1.563570e-05  
1             0.0      86.8   0.184355    4.102517e-06  
2            18.1     124.5   0.194544    9.801555e-05  
3             0.0       0.0   0.487447    8.073226e-07  
4            -1.0      -1.0   0.214633    2.454920e-06  
...           ...       ...        ...             ...  
55362         0.0     249.0   0.331501    1.036090e-02  
55363        -1.0      -1.0   0.124683    1.167611e-01  
55364         0.0       0.0   0.097682    9.393759e-03  
55365        -1.0      -1.0   0.178206    5.371974e-03  
55366         0.0      18.8   0.167305    1.253269e-01  

[55367 rows x 44 columns]

In [163]:
import folium
from folium.plugins import HeatMap, HeatMapWithTime

map_obj = folium.Map(location = [38.27312, -98.5821872], zoom_start = 4)


df['latitude'] = df['latitude'].astype(float)
df['longitude'] = df['longitude'].astype(float)

df_onlylarge = df[df['fire_mag'] >= 10.0]
df_heat = df_onlylarge[['longitude','latitude', 'fire_size_norm', 'disc_clean_date']]

# List comprehension to make out list of lists
heat_data = [[row['latitude'],row['longitude'],row['fire_size_norm']] for index, row in df_heat.iterrows()]
heat_time_dates =  [[row['disc_clean_date']] for index, row in df_heat.iterrows()]

HeatMap(heat_data, radius=10, blur=10).add_to(map_obj)

map_obj


In [164]:
import math
for i in range(0, len(df_onlylarge)):
    radius = math.sqrt((df_onlylarge.iloc[i]['fire_size']*4046.856422)/math.pi)
    folium.Circle(
    location = [df_onlylarge.iloc[i]['latitude'], df_onlylarge.iloc[i]['longitude']],
    radius = radius,
    tooltip = '<li><bold> Fire size: ' + str(df_onlylarge.iloc[i]['fire_size']) + ' acres' + 
              '<li><bold> Fire size class: ' + str(df_onlylarge.iloc[i]['fire_size_class']) +
              '<li><bold> Date: ' + str(df_onlylarge.iloc[i]['disc_clean_date'])
              
    ).add_to(map_obj)

In [165]:
map_obj

In [180]:
import plotly.graph_objects as go
df4 = copy.copy(df[['state', 'fire_size']])

df4 = df4.groupby('state').count().reset_index()
df4
fig = go.Figure(data=go.Choropleth(
    locations=df4['state'], # Spatial coordinates
    z = df4['fire_size'].astype(float), # Data to be color-coded
    locationmode = 'USA-states', # set of locations match entries in `locations`
    colorscale = 'Reds',
    colorbar_title = "Amount of forest fires",
))

fig.update_layout(
    title_text = 'Forest fires per state',
    geo_scope='usa', # limite map scope to USA
)

fig.show()